# コードを使用したエージェントワークフロー

このノートブックでは、DataRobotのシンプルなエージェントワークフローを示し、MLOpsを使用してワークフローを提供、監視、およびガバナンスする方法を紹介します。


このノートブックを実行すると、基本的な演算も確実に実行できるシンプルなエージェントの DataRobot MLOpsデプロイが作成されます。また、この例では、エージェントが使用する電卓ツールのデプロイも別途作成します。


## コードアセットの概要

このワークフローでは、以下のコードベースのアセットが使用されます。これらはすべて[こちら](https://s3.amazonaws.com/datarobot_public_datasets/ai_accelerators/simple_agent/simple_agent.zip)からダウンロードできます。


- `calculator/custom.py`：LLMが簡単な算術演算を確実に実行できるようにする「電卓」ツールのカスタムデプロイロジック。

- `agent/custom.py`：ユーザープロンプトに直接回答するか、または最初に電卓ツールに任せるエージェントのカスタムデプロイロジック。

- `agent/requirements.txt`：エージェントのカスタムデプロイのためのPythonの依存関係。

- `agent/model-metadata.yaml`：Azure OpenAIの資格情報と電卓デプロイの識別子を指定するエージェントデプロイの構成ファイル。

- `create_deployments.ipynb`：このノートブックファイル。デプロイを作成してテストするためのコードが含まれています。


## ワークフローの概要

1. 電卓のデプロイを作成

2. エージェントのデプロイのためにmodel-metadata.yamlを更新

3. エージェントのデプロイを作成

4. エージェントのデプロイを使用して予測のテストと実行


## 1. 電卓のデプロイを作成

以下のセルはcalculatorディレクトリ(`calculator/custom.py`)内のファイルをデプロイします。DataRobotパッケージをインポートし、DataRobot MLOpsのデプロイ作成方法を使って、カスタムモデルのデプロイを作成します。このモデルは電卓として機能します。デプロイに2つの数値と数学演算子を取り込むと、モデルは答えを返します。


In [1]:
import datarobot as dr

default_prediction_server_id='5a61d7a0fbd723001a2f70d9' # Specify your prediction server here

cm_calc = dr.CustomInferenceModel.create(name='Calculator',
                                    target_name='result',
                                    target_type='TextGeneration')
cmv_calc = dr.CustomModelVersion.create_clean(cm_calc.id,
                                         base_environment_id='5e8c889607389fe0f466c72d', # 3.9 drop-in
                                         folder_path='./calculator')
rmv_calc = dr.RegisteredModelVersion.create_for_custom_model_version(cmv_calc.id)
d_calc = dr.Deployment.create_from_registered_model_version(rmv_calc.id, 
                                                       'Calculator', 
                                                       default_prediction_server_id=default_prediction_server_id)

## 2. 資格情報の指定

任意のテキストエディターで、Azure Open AIの資格情報と、手順1で作成した電卓デプロイのデプロイIDで`agent/model-metadata.yaml`を更新します。本番環境では、DataRobot資格情報ストアを使用して、デプロイ内のシークレットを公開する必要があります。この手順は、この例を簡潔にするために省略しています。


## 3. エージェントのデプロイを作成

以下のコードを使用して、エージェントのデプロイを作成します。


In [ ]:
cm_agent = dr.CustomInferenceModel.create(name='Agent',
                                    target_name='completion',
                                    target_type='TextGeneration')
cmv_agent = dr.CustomModelVersion.create_clean(cm_agent.id,
                                               base_environment_id='5e8c889607389fe0f466c72d', # 3.9 drop-in,
                                               folder_path='./agent')
dr.CustomModelVersionDependencyBuild.start_build(cm_agent.id, cmv_agent.id)
rmv_agent = dr.RegisteredModelVersion.create_for_custom_model_version(cmv_agent.id)
d_agent = dr.Deployment.create_from_registered_model_version(rmv_agent.id, 
                                                             'Agent', 
                                                              default_prediction_server_id=default_prediction_server_id)

## 4. デプロイのテスト

以下のセルは、電卓モデルに算数の問題（`What is 4 x 752`）を出し、エージェントが取得した回答を受け取ることで、デプロイとやり取りします。


In [40]:
from datarobot_predict.deployment import predict
import pandas as pd
import json

messages = [
    {'role': 'user',
     'content': 'what is 4*752',}
]
df, _ = predict(d_agent, pd.DataFrame([{'messages': json.dumps(messages)}]))
df

In [ ]:
messages = [
    {'role': 'user',
     'content': 'hello',}
]
df, _ = predict(d_agent, pd.DataFrame([{'messages': json.dumps(messages)}]))
df